### Дополнительно домашнее задание 1 - 10 баллов

1. Загрузите набор данных lenta-ru-news с помощью библиотеки Corus для задачи классификации текстов по топикам
2. Опишите, насколько, по вашему мнению, данные требуют предобработки для задачи тематического моделирования. При необходимости, проведите релевантную предобработку текстов. **1 балл**
3. Используйте библиотеку BERTopic для тематического моделирования:
    - Подберите оптимальные, на ваш взгляд, элементы пайплайна: энкодер, снижение размерности, алгоритм кластеризации, способ токенизации, постобработку/тюнинг. 
При выборе инструмента на каждом шаге опишите, почему был выбран именно он среди многочисленных альтернатив. **2 балла**
    - Настройте ваш пайплайн, подобрав оптимальные гиперпараметры для отдельных шагов. При выборе значений конкретных гиперпараметров укажите, почему остановились на тех или иных значениях. **1 балл**
4. Визуализируйте полученные результаты: **2 балла**
    - Топ-токены для каждого топика.
    - Документы с их топиками в 2D пространстве
    - Распределение тем по токенам для выборочных текстов из датасета
5. Оцените формальное качество лучшего результата с помощью метрик для тематического моделирования:  **2 балла**
    - Topic Diversity
    - UMass Coherence
Hint: реализацию можно написать самостоятельно или поискать в таких библиотеках, как [Gensim](https://github.com/piskvorky/gensim) и [OSTIS](https://github.com/MIND-Lab/OCTIS)
6. Проанализируйте полученные результаты в совокупности и резюмируйте, что удалось, какие проблемы вы заметили, как их можно решить в дальнейшем. **1 балл**



**Общее**

- Обеспечена воспроизводимость решения: зафиксированы random_state, ноутбук воспроизводится от начала до конца без ошибок - **1 балл**

**Формат сдачи ДЗ**

- Каждая домашняя работа – PR в отдельную ветку **hw_add_n**, где **n** - номер домашней работы
- Добавить ментора и pacifikus в reviewers
- Дождаться ревью, если все ок – мержим в main
- Если не ок – вносим исправления и снова отправляем на ревью

In [14]:
import pickle
import random
import re

import hdbscan
import nltk
import numpy as np
import pandas as pd
import spacy
from bertopic import BERTopic
from gensim.corpora.dictionary import Dictionary
from gensim.models.coherencemodel import CoherenceModel
from nltk.corpus import stopwords
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from bertopic.vectorizers import ClassTfidfTransformer
from umap import UMAP


RANDOM_STATE = 42
np.random.seed(RANDOM_STATE)
random.seed(RANDOM_STATE)

### 1. Загрузка и предобработка

In [ ]:
# данные требуют предобработки, чтобы улучшить качество тематического моделирования:
# 1. удаление чисел и знаков препинания, которые не несут смысловой нагрузки.
# 2. токенизация текста: разделение на слова.
# 3. удаление стоп-слов, чтобы избежать влияния частых, но неинформативных слов.
# 4. лемматизация для приведения слов к начальной форме (чтобы темы не зависели от формы слова).

# в hw_1 я уже писала код параллельной предобработки текстов, сохранив при этом обработанный
# датасет из 100_000 текстов, поэтому просто загружу его, чтобы не делать это второй раз

In [ ]:
texts = pd.read_csv("data/translation/clean_lenta-ru-news.csv")["lemmatized_text"].tolist()
for i in range(3):
    print(texts[i], "\n")

вица премьер социальный вопрос татьяна голикова рассказывать какой регион россия зафиксировать наиболее высокий смертность рак сообщать риа новость слово голикова чаща онкологический заболевание становиться причина смерть псковский тверская тульский орловский область также севастополь вица премьер напоминать главный фактор смертность россия рак болезнь система кровообращение начало год становиться известно смертность онкологический заболевание среди россиянин снижаться впервые год данные росстат год рак умирать тысяча человек это процент маленький год ранее 

австрийский правоохранительный орган представлять доказательство нарушение российский биатлонист антидопинговый правило сообщать посол россия вена дмитрий любинский итог встреча уполномоченный адвокат дипмиссия представитель прокуратура страна передавать тасс действовать презумпция невиновность какой либо ограничение свобода передвижение команда добавлять посольство международный союз биатлонист также применять санкция российский 

### 2. BERTopic

In [ ]:
# модель BERT для расчетов эмбеддингов предложений на русском языке.
# основана на cointegrated/LaBSE-en-ru - имеет аналогичные размеры контекста (512),
# ембеддинга (768) и быстродействие. использовала в рабочей задаче,
# поэтому остановилась на ней

embedding_model = SentenceTransformer("sergeyzh/LaBSE-ru-turbo")

modules.json:   0%|          | 0.00/368 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.1k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/56.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/887 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/513M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.29k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/576k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/732 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/196 [00:00<?, ?B/s]

In [ ]:
embeddings = embedding_model.encode(texts, batch_size=64, show_progress_bar=True, use_gpu=True)

with open("data/topic_modelling/embeddings_100000.pkl", "wb") as file:
    pickle.dump(embeddings, file)

Batches:   0%|          | 0/1563 [00:00<?, ?it/s]

In [ ]:
with open("data/topic_modelling/embeddings_100000.pkl", "rb") as file:
    embeddings = pickle.load(file)

In [ ]:
# выбрала countvectorizer, потому что он простой и понятный, хорошо работает с bertopic.
vectorizer_model = CountVectorizer(
    min_df=0.01,  # чтобы выкинуть редкие слова, которые встречаются меньше чем в 1% текстов.
    max_df=0.95,  # убираем слишком частые слова, которые почти везде, от них мало пользы.
)

# для понижения размерности взяла umap — он сохраняет локальную структуру данных,
# работает лучше pca или tsne, особенно когда нужно потом кластеризовать.
umap_model = UMAP(
    n_neighbors=20,  # базовое значение, чтобы учитывать локальные связи, но не терять глобальную картину.
    n_components=10,  # на практике показало хорошие результаты, тем хватает, без сильной потери информации
    min_dist=0.0,  # чтобы точки можно было собирать плотнее, это помогает отделить кластеры.
    metric="cosine",  # косинус хорошо работает с текстовыми эмбеддингами.
    random_state=RANDOM_STATE,
)

# взяла hdbscan, потому что он не требует заранее указывать число кластеров,
# плюс умеет находить кластеры разной формы и сам определяет, что шум.
hdbscan_model = hdbscan.HDBSCAN(
    min_cluster_size=50,  # чтобы не ловить слишком мелкие и шумовые группы, а выделять только основные.
    metric="euclidean",  # работает хорошо в пониженной размерности.
    prediction_data=True,
)

# ctfidf transformer нужен, чтобы считать tf-idf с учетом информации о теме.
ctfidf_model = ClassTfidfTransformer(
    reduce_frequent_words=True  # автоматически убирает суперчастотные слова, что улучшает читаемость тем.
)

topic_model = BERTopic(
    embedding_model=embedding_model,
    umap_model=umap_model,
    hdbscan_model=hdbscan_model,
    vectorizer_model=vectorizer_model,
    ctfidf_model=ctfidf_model,
    language="russian",
    calculate_probabilities=True,  # чтобы понимать, насколько уверенно модель отнесла текст к теме.
    verbose=True,
)

topics, probs = topic_model.fit_transform(texts, embeddings)

2025-04-16 15:39:10,691 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2025-04-16 15:41:38,861 - BERTopic - Dimensionality - Completed ✓
2025-04-16 15:41:38,865 - BERTopic - Cluster - Start clustering the reduced embeddings
2025-04-16 15:50:53,974 - BERTopic - Cluster - Completed ✓
2025-04-16 15:50:54,076 - BERTopic - Representation - Fine-tuning topics using representation models.
2025-04-16 15:51:02,859 - BERTopic - Representation - Completed ✓


### 3. Визуализация

In [ ]:
topic_model.visualize_barchart(top_n_topics=8)

In [16]:
topic_model.get_topic_info().head(10)

Topic  Count                                   Name  \
0     -1  33275          -1_водитель_проверка_форум_рф   
1      0   5305            0_футболист_матч_футбол_мяч   
2      1   2644      1_ученый_исследователь_клетка_ген   
3      2   2521        2_животное_собака_акула_зоопарк   
4      3   1960  3_авиакомпания_рейс_пассажир_аэрофлот   
5      4   1249     4_истребитель_су_миг_гиперзвуковой   
6      5   1241     5_коллекция_обувь_аксессуар_одежда   
7      6   1234        6_бой_макгрегор_поединок_нокаут   
8      7   1128      7_юзер_пользователь_блогер_парень   
9      8    991       8_стрельба_тюрьма_штат_грабитель   

                                      Representation  \
0  [водитель, проверка, форум, рф, свобода, ребен...   
1  [футболист, матч, футбол, мяч, футбольный, сбо...   
2  [ученый, исследователь, клетка, ген, планета, ...   
3  [животное, собака, акула, зоопарк, змея, кроко...   
4  [авиакомпания, рейс, пассажир, аэрофлот, аэроп...   
5  [истребитель, су, миг, гиперзвуковой, поколени...   
6  [коллекция, обувь, аксессуар, одежда, бренд, м...   
7  [бой, макгрегор, поединок, нокаут, боксер, бок...   
8  [юзер, пользователь, блогер, парень, подписчик...   
9  [стрельба, тюрьма, штат, грабитель, ученик, шк...   

                                 Representative_Docs  
0  [индекс опора зафиксировать незначительный рос...  
1  [полузащитник реал сборная хорватия лук модрич...  
2  [американский ученый изучать загадочный источн...  
3  [таиландский провинция чаченгсау поймать питон...  
4  [течение два неделя компания вим авиа урегулир...  
5  [риа новость называть пять прототип советский ...  
6  [модный бренд объявлять предстоящий выпуск сов...  
7  [бывший чемпион мир бокс версия международный ...  
8  [пользователь сеть разделяться лагерь увидеть ...  
9  [николас круз расстреливать винтовка ученик од...

In [ ]:
import numpy as np
import plotly.io as pio

sample_indices = np.random.choice(len(texts), size=3, replace=False)

for i, idx in enumerate(sample_indices, 1):
    fig = topic_model.visualize_distribution(
        probs[idx][:50], title=f"документ {i}: {texts[idx][:40]}...", min_probability=0.001
    )
    pio.show(fig)

In [43]:
reduced_embeddings = umap_model.fit_transform(embeddings)
topic_model.visualize_documents(
    texts,
    topics=topics[:10],
    reduced_embeddings=reduced_embeddings,
    sample=0.03,
)

### 4. Метрики

In [ ]:
def calc_topic_diversity(topic_dict, top_k=10):
    top_terms = []
    for topic_id in topic_dict:
        top_words = [term for term, _ in topic_dict[topic_id][:top_k]]
        top_terms += top_words
    unique_terms = set(top_terms)
    total_terms = len(topic_dict) * top_k
    return len(unique_terms) / total_terms


topics_data = topic_model.get_topics()
div_score = calc_topic_diversity(topics_data)
print("topic diversity:", round(div_score, 4))

topic diversity: 0.8877


In [42]:
texts_tokens = [doc.split() for doc in texts]
topics_gensim = [
    [word for word, _ in topic_model.get_topic(topic_id)[:10]]
    for topic_id in topic_model.get_topics().keys()
    if topic_id != -1
]

coherence_model = CoherenceModel(
    topics=topics_gensim,
    texts=texts_tokens,
    dictionary=Dictionary(texts_tokens),
    coherence="u_mass",
)

umass_score = coherence_model.get_coherence()
print("UMass Coherence:", umass_score)

UMass Coherence: -2.8955044972256982


In [ ]:
print(f"Найдено тем: {len(topic_model.get_topics()) - 1}")
print(f"Topic Diversity: {div_score:.3f}")
print(f"UMass Coherence: {umass_score:.3f}")

# в целом, bertopic неплохо справился с выделением осмысленных тем из русскоязычных политических новостей.
# настройки подбирала в основном эмпирически, и на выходе получилось довольно разнообразное тематическое пространство
# - topic diversity получился высоким, что ожидаемо при таком объёме текстов.

# тем не менее, чувствуется некоторая "дробленость" — тем больше, чем нужно, и многие из них очень близки по смыслу.
# возможно, стоит уменьшить общее количество топиков: либо напрямую через агрегацию схожих тем, либо более агрессивной настройкой `min_cluster_size` в hdbscan.
# ещё вариант — чуть повысить `n_neighbors` в umap, чтобы больше учитывать глобальную структуру.

# что касается связности, показатель UMass coherence получился около -2.9, что не критично, но всё же указывает на то,
# что часть тем могли бы быть более "плотными" по смыслу. это можно попробовать улучшить за счёт донастройки гиперпараметров
# - например, изменить min_df у векторизатора или попробовать другой тип эмбеддингов (например, тот же rubert, затюненный на новости).

# в качестве следующего шага имеет смысл:
# - попробовать сократить количество тем до более компактного числа (например, 20–30, не больше);
# - переобучить модель на более качественных эмбеддингах;
# - или вручную сгруппировать мелкие темы с высокой схожестью.

# PS. все картинки добавила в папку pictures, тк git не отображает выход ноутбуков

Найдено тем: 252
Topic Diversity: 0.888
UMass Coherence: -2.896
